In [ ]:
!pip install torch transformers datasets accelerate bitsandbytes
!pip install unsloth
!pip install peft

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 66.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 52.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 31.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 11.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 6.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 51.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 484.9/484.9 kB 28.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.7/69.7 MB 8.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 

In [ ]:
!pip install torch transformers datasets accelerate bitsandbytes
!pip install unsloth
!pip install peft

In [ ]:
!pip install huggingface_hub

In [ ]:
from huggingface_hub import notebook_login
notebook_login()

In [ ]:
import torch

print(f"CUDA Available: {torch.cuda.is_available()}")
if torch.cuda.is_available():
    print(f"GPU Device: {torch.cuda.get_device_name(0)}")


In [ ]:
import pandas as pd
from google.colab import files

# Upload the dataset
uploaded = files.upload()

# Load dataset
dataset = pd.read_excel('telugu.xlsx')

# Display the first few rows of the dataset
print(dataset.head())
print(dataset.columns)

In [ ]:
from transformers import AutoTokenizer

# Initialize the tokenizer
tokenizer = AutoTokenizer.from_pretrained('TinyLlama/TinyLlama-1.1B-Chat-v1.0')

In [ ]:
!pip install datasets


In [ ]:
from datasets import Dataset

# Convert pandas DataFrame to Hugging Face Dataset
hf_dataset = Dataset.from_pandas(dataset)


In [ ]:
# Define the preprocessing function
def preprocess_function(examples):
    # Ensure examples['text'] is a list of strings
    texts = [str(text) for text in examples['text']]
    return tokenizer(texts, truncation=True, max_length=128, padding='max_length')

# Apply the preprocessing function to the Hugging Face Dataset
tokenized_datasets = hf_dataset.map(preprocess_function, batched=True)


Map:   0%|          | 0/501 [00:00<?, ? examples/s]

In [ ]:
from transformers import AutoModelForCausalLM
from peft import LoraConfig, get_peft_model

model_name = "TinyLlama/TinyLlama-1.1B-Chat-v1.0"
model = AutoModelForCausalLM.from_pretrained(model_name)

lora_config = LoraConfig(
    r=16,
    lora_alpha=32,
    target_modules=["q_proj", "k_proj", "v_proj", "o_proj"],
    lora_dropout=0.05,
    bias="none",
    task_type="CAUSAL_LM"
)

model = get_peft_model(model, lora_config)
model.enable_input_require_grads()
model.gradient_checkpointing_enable()


In [ ]:
from transformers import TrainingArguments

training_args = TrainingArguments(
    output_dir="./results",
    eval_strategy="epoch",  # Change to `eval_strategy`
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=3,
    weight_decay=0.01,
    save_total_limit=2,
    load_best_model_at_end=True,
    save_strategy="epoch"  # Ensure it matches the eval_strategy
)

In [ ]:
from transformers import DataCollatorForLanguageModeling

data_collator = DataCollatorForLanguageModeling(
    tokenizer=tokenizer,
    mlm=False,
)


In [ ]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_datasets,
    eval_dataset=tokenized_datasets,
    data_collator=data_collator,
    tokenizer=tokenizer,
)

<ipython-input-24-0c029fa21263>:3: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


In [ ]:
trainer.train()

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Currently logged in as: gsramya2005 (gsramya2005-hkbk-college-of-engineering) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`.


TrainOutput(global_step=96, training_loss=0.9668324788411459, metrics={'train_runtime': 483.0275, 'train_samples_per_second': 3.112, 'train_steps_per_second': 0.199, 'total_flos': 1199342615003136.0, 'train_loss': 0.9668324788411459, 'epoch': 3.0})

In [ ]:
trainer.evaluate()

{'eval_loss': 3.4542908668518066,
 'eval_runtime': 42.941,
 'eval_samples_per_second': 11.667,
 'eval_steps_per_second': 0.745,
 'epoch': 3.0}

In [ ]:
model.save_pretrained("telugu_model")
tokenizer.save_pretrained("telugu_model")

('telugu_model/tokenizer_config.json',
 'telugu_model/special_tokens_map.json',
 'telugu_model/tokenizer.model',
 'telugu_model/added_tokens.json',
 'telugu_model/tokenizer.json')

In [ ]:
from transformers import TrainingArguments

training_args = TrainingArguments(
    output_dir="./results",
    eval_strategy="epoch",  # Change to `eval_strategy`
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=3,
    weight_decay=0.01,
    save_total_limit=2,
    load_best_model_at_end=True,
    save_strategy="epoch"  # Ensure it matches the eval_strategy
)

In [ ]:
from transformers import DataCollatorForLanguageModeling

data_collator = DataCollatorForLanguageModeling(
    tokenizer=tokenizer,
    mlm=False,
)

In [ ]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_datasets,
    eval_dataset=tokenized_datasets,
    data_collator=data_collator,
    tokenizer=tokenizer,
)

<ipython-input-30-0c029fa21263>:3: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


In [ ]:
trainer.train()

TrainOutput(global_step=96, training_loss=0.48191014925638836, metrics={'train_runtime': 485.1496, 'train_samples_per_second': 3.098, 'train_steps_per_second': 0.198, 'total_flos': 1199342615003136.0, 'train_loss': 0.48191014925638836, 'epoch': 3.0})

In [ ]:
trainer.evaluate()

{'eval_loss': 0.3767460286617279,
 'eval_runtime': 42.3501,
 'eval_samples_per_second': 11.83,
 'eval_steps_per_second': 0.756,
 'epoch': 3.0}

In [ ]:
model.save_pretrained("telugu_model")
tokenizer.save_pretrained("telugu_model")

('telugu_model/tokenizer_config.json',
 'telugu_model/special_tokens_map.json',
 'telugu_model/tokenizer.model',
 'telugu_model/added_tokens.json',
 'telugu_model/tokenizer.json')

In [ ]:
from transformers import TrainingArguments

training_args = TrainingArguments(
    output_dir="./results",
    eval_strategy="epoch",  # Changed to `eval_strategy`
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=3,
    weight_decay=0.01,
    save_total_limit=2,
    load_best_model_at_end=True,
    save_strategy="epoch"  # Ensure it matches the eval_strategy
)

In [ ]:
from transformers import DataCollatorForLanguageModeling

data_collator = DataCollatorForLanguageModeling(
    tokenizer=tokenizer,
    mlm=False,
)

In [ ]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_datasets,
    eval_dataset=tokenized_datasets,
    data_collator=data_collator,
    tokenizer=tokenizer,
)

<ipython-input-36-0c029fa21263>:3: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


In [ ]:
trainer.train()

TrainOutput(global_step=96, training_loss=0.3950839837392171, metrics={'train_runtime': 485.6068, 'train_samples_per_second': 3.095, 'train_steps_per_second': 0.198, 'total_flos': 1199342615003136.0, 'train_loss': 0.3950839837392171, 'epoch': 3.0})

In [ ]:
trainer.evaluate()

{'eval_loss': 0.32560598850250244,
 'eval_runtime': 42.5156,
 'eval_samples_per_second': 11.784,
 'eval_steps_per_second': 0.753,
 'epoch': 3.0}

In [ ]:
model.save_pretrained("telugu_model")
tokenizer.save_pretrained("telugu_model")

('telugu_model/tokenizer_config.json',
 'telugu_model/special_tokens_map.json',
 'telugu_model/tokenizer.model',
 'telugu_model/added_tokens.json',
 'telugu_model/tokenizer.json')

In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained("telugu_model")
model = AutoModelForCausalLM.from_pretrained("telugu_model")

In [ ]:
# Define the input text
input_text = "మీరు ఏమిటి చేస్తున్నారు?"

# Tokenize the input text
inputs = tokenizer(input_text, return_tensors="pt")

# Generate the output with `max_new_tokens` parameter
outputs = model.generate(**inputs, max_new_tokens=50, num_return_sequences=1)

# Decode the output
generated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)

print(generated_text)


మీరు ఏమిటి చేస్తున్నారు? మీరు కొత్త ప్రాజెక్��


In [ ]:
from flask import Flask, request, jsonify
from transformers import AutoModelForCausalLM, AutoTokenizer

app = Flask(__name__)

# Load the tokenizer and model
tokenizer = AutoTokenizer.from_pretrained("telugu_model")
model = AutoModelForCausalLM.from_pretrained("telugu_model")

@app.route('/generate', methods=['POST'])
def generate_text():
    data = request.json
    input_text = data.get('input_text', '')
    inputs = tokenizer(input_text, return_tensors="pt")
    outputs = model.generate(**inputs, max_new_tokens=50, num_return_sequences=1)
    generated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)
    return jsonify({'generated_text': generated_text})

if __name__ == '__main__':
    app.run(debug=True)
